In [81]:
import sys
import os
# Add the project root directory to the Python path
sys.path.append(os.path.abspath('..'))

# Import functions
from scripts.lorenz96_1d import lorenz96, lorenz96_rk4_step

import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation, rc
from IPython.display import Image
from tqdm import tqdm


# Enable interactive plotting in Jupyter notebooks
%matplotlib inline

np.random.seed(42)

In [120]:
def particle_filter_lorenz96(X, Y, H, R, F, dt, num_particles):
    state_dim = X.shape[1]
    obs_dim = Y.shape[0]

    # Propagate particles using the Lorenz 96 model with RK4 integration
    for i in range(num_particles):
        X[i] = lorenz96_rk4_step(X[i], F, dt)

    # Calculate the likelihood of each particle given the observations
    weights = np.zeros(num_particles)
    for i in range(num_particles):
        pred_obs = H @ X[i]  # Project state space into observation space
        innov = Y - pred_obs  # Innovation in the observation space
        weights[i] = np.exp(-0.5 * np.dot(innov.T, np.linalg.solve(R, innov)))

    # Normalize the weights
    weights /= np.sum(weights)
    
    # Ensure weights are valid
    if np.sum(weights) == 0 or np.isnan(np.sum(weights)):
        weights.fill(1.0 / num_particles)

    # Resample particles based on weights
    indices = np.random.choice(num_particles, num_particles, p=weights)
    X_resampled = X[indices]

    # Add variability to the particles after resampling
    X_resampled += np.random.randn(*X_resampled.shape) * 0.01

    return X_resampled, weights

In [129]:
# Parameters
N = 40  # Number of state variables
num_particles = 300
state_dim = N
obs_dim = 25 # Number of 'observation stations'
obs_std = 1 # Standard deviation of the observations
F = 8.0
dt = 0.01
num_steps = 500

# Initial conditions
x0 = F * np.ones(N)
x0 += np.random.randn(N) * 0.1  # Small perturbation for all states
particles = np.array([x0 + np.random.randn(N) * 0.1 for _ in range(num_particles)]).T

# Create observations and run particle filter
observation_indices = np.random.choice(N, obs_dim, replace=False)  # Randomly select 25 state indices
observations = np.full((num_steps, N), np.nan)  # Initialize observations array with NaNs

# Observation operator (projection matrix)
H = np.zeros((obs_dim, state_dim))
for i, idx in enumerate(observation_indices):
    H[i, idx] = 1

# Observation error covariance
R = np.eye(obs_dim) * obs_std**2

# Lists to store true states, particle states, and observations
true_states = []
particle_states = []
all_observations = []

# Run particle filter and generate observations in one loop
true_state = x0.copy()
X = ensembles.T
for step in range(num_steps):
    # Propagate true state
    true_state = lorenz96_rk4_step(true_state, F, dt)
    true_states.append(true_state.copy())

    # Propagate particles
    for i in range(num_particles):
        X[i] = lorenz96_rk4_step(X[i], F, dt)
    
    if step % 20 == 0:
        # Generate synthetic observations
        Y = true_state[observation_indices] + np.random.multivariate_normal(np.zeros(obs_dim), R)
        observations[step, observation_indices] = Y
        all_observations.append(Y)

        # Run particle filter update step
        X, weights = particle_filter_lorenz96(X, Y, H, R, F, dt, num_particles)
        #print(f"Time step {step}, Weights: {weights}")
    
    # Store particle states for later plotting
    particle_states.append(X.copy())
    
#particle_means = np.mean(particle_states, axis=1)

/var/folders/y9/k7_31tzx3n722ngkv6__qnhc0000gn/T/ipykernel_28640/178785207.py:17: RuntimeWarning: invalid value encountered in divide
  weights /= np.sum(weights)


In [130]:
def create_animation(true_states, particle_states, observations, N, num_particles, num_steps):
    # First set up the figure, the axis, and the plot element we want to animate
    fig, ax = plt.subplots(figsize=(10, 5))  # Adjust the figsize parameter for a rectangular figure
    plt.close()

    ax.set_xlim((0, N - 1))
    ax.set_ylim((np.min(particle_states), np.max(particle_states)))

    # Initialize lines
    true_line, = ax.plot([], [], 'r-', lw=2, label='Model')
    mean_line, = ax.plot([], [], 'b-', lw=2, alpha=0.7, label='Particle Mean')
    observation_scatter = ax.scatter([], [], c='k', marker='*', s=100, label='Observations', zorder=5)

    # Set axes titles
    ax.set_xlabel('k')
    ax.set_ylabel(r'$X_k$')
    ax.legend(loc='upper right')

    # Initialization function: plot the background of each frame
    def init():
        true_line.set_data([], [])
        mean_line.set_data([], [])
        observation_scatter.set_offsets(np.empty((0, 2)))
        return [true_line, mean_line, observation_scatter]

    # Animation function. This is called sequentially
    def animate(i):
        x = np.arange(N)
        true_line.set_data(x, true_states[i])
        
        particle_mean = np.mean(particle_states[i], axis=0)
        mean_line.set_data(x, particle_mean)

        # Update observations
        obs_indices = np.where(~np.isnan(observations[i]))[0]
        if len(obs_indices) > 0:
            obs_values = observations[i, obs_indices]
            observation_scatter.set_offsets(np.c_[obs_indices, obs_values])
            observation_scatter.set_visible(True)
        else:
            observation_scatter.set_visible(False)

        ax.set_title(f'Time step: {i}')
        return [true_line, mean_line, observation_scatter]

    # Generate the frames list for every 20 time steps
    frames = list(range(0, num_steps, 15))

    # Call the animator
    anim = animation.FuncAnimation(fig, animate, init_func=init,
                                   frames=frames, interval=250, blit=True)

    # This part makes it work on Colab
    rc('animation', html='jshtml')
    anim.save('lorenz96_particle_filter.gif', writer='pillow', fps=5)
    return anim

# Call the animation function
anim = create_animation(true_states, particle_states, observations, N, num_particles, num_steps)
anim


In [131]:
# Call the animation function
anim = create_animation(true_states, particle_states, observations, N, num_particles, num_steps)
anim

In [106]:
def run_particle_filter(num_particles, N=40, obs_dim=25, obs_std=1, F=8.0, dt=0.01, num_steps=500):
    # Initial conditions
    x0 = F * np.ones(N)
    x0 += np.random.randn(N) * 0.1  # Small perturbation for all states
    particles = np.array([x0 + np.random.randn(N) * 0.1 for _ in range(num_particles)]).T

    # Create observations and run particle filter
    observation_indices = np.random.choice(N, obs_dim, replace=False)  # Randomly select 25 state indices
    observations = np.full((num_steps, N), np.nan)  # Initialize observations array with NaNs

    # Observation operator (projection matrix)
    H = np.zeros((obs_dim, N))
    for i, idx in enumerate(observation_indices):
        H[i, idx] = 1

    # Observation error covariance
    R = np.eye(obs_dim) * obs_std**2

    # Lists to store true states, particle states, and observations
    true_states = []
    particle_states = []
    all_observations = []

    # Run particle filter and generate observations in one loop
    true_state = x0.copy()
    X = particles.T
    for step in tqdm(range(num_steps), desc="Processing steps"):
        # Propagate true state
        true_state = lorenz96_rk4_step(true_state, F, dt)
        true_states.append(true_state.copy())

        # Propagate particles
        for i in range(num_particles):
            X[i] = lorenz96_rk4_step(X[i], F, dt)
        
        if step % 20 == 0:
            # Generate synthetic observations
            Y = true_state[observation_indices] + np.random.multivariate_normal(np.zeros(obs_dim), R)
            observations[step, observation_indices] = Y
            all_observations.append(Y)

            # Run particle filter update step
            X, weights = particle_filter_lorenz96(X, Y, H, R, F, dt, num_particles)

        # Store particle states for later plotting
        particle_states.append(X.copy())

    # Convert lists to numpy arrays for easier manipulation
    true_states = np.array(true_states)
    particle_states = np.array(particle_states)
    observations = np.array(observations)

    # Calculate the mean of the particles for each point in time
    particle_means = np.mean(particle_states, axis=1)

    # Calculate the square-root distance metric
    distance_metric = np.sqrt(np.sum((true_states - particle_means)**2, axis=1))

    # Sum all these values into one to get a single metric
    total_difference = np.sum(distance_metric)

    return total_difference

In [100]:
# Example usage:
num_particles = 70
total_diff = run_particle_filter(num_particles)
print(f'Total difference between true states and particle means: {total_diff}')

Processing steps: 100%|██████████████████████| 500/500 [00:04<00:00, 123.72it/s]

Total difference between true states and particle means: 15018.991681471798


In [124]:
particle_numbers = [10, 100, 200, 300, 1000]  # List of different particle numbers to test
results = []  # List to store tuples of (particle_number, total_difference)

for num_particles in particle_numbers:
    total_diff = run_particle_filter(num_particles)
    results.append((num_particles, total_diff))
    outer.set_postfix({"Total difference": total_diff})
    print(f'Particle number: {num_particles}, Total difference: {total_diff}')

Processing steps: 100%|██████████████████████| 500/500 [00:00<00:00, 702.03it/s]


Particle number: 10, Total difference: 16431.780843275486


Processing steps:  23%|█████▏                 | 114/500 [00:01<00:04, 80.29it/s]/var/folders/y9/k7_31tzx3n722ngkv6__qnhc0000gn/T/ipykernel_28640/178785207.py:17: RuntimeWarning: invalid value encountered in divide
  weights /= np.sum(weights)
Processing steps: 100%|███████████████████████| 500/500 [00:06<00:00, 79.08it/s]


Particle number: 100, Total difference: 16126.446817362557


Processing steps: 100%|███████████████████████| 500/500 [00:12<00:00, 39.41it/s]


Particle number: 200, Total difference: 15791.945069485515


Processing steps: 100%|███████████████████████| 500/500 [00:19<00:00, 26.10it/s]


Particle number: 300, Total difference: 14996.504797118429


Processing steps: 100%|███████████████████████| 500/500 [01:03<00:00,  7.93it/s]

Particle number: 1000, Total difference: 14706.950964757754


In [54]:
particle_means.shape

(500, 40)

In [64]:
stt = np.array(true_states)

In [58]:
particle_states[1].shape

(1000, 40)

In [65]:
dist = np.sqrt(stt -)

(500, 40)